In [1]:
import pandas as pd
import numpy as np
import pickle
import re
import pyarrow.parquet as pq
from pyspark.sql import SparkSession

spark = SparkSession \
    .builder \
    .appName('Python Spark SQL basic example') \
    .config('spark.some.config.option', 'some-value') \
    .getOrCreate()

pd.set_option('display.max_columns', 40)
pd.set_option('display.max_rows', 5000)


In [2]:
#df_2002 = spark.read.parquet('census_02.parquet')
#df_2007 = spark.read.load('census_07.parquet')
#df_2012 = spark.read.load('census_12.parquet')

In [30]:
#df_2002.limit(5).toPandas().head()

SOURCE_DESC SECTOR_DESC   GROUP_DESC COMMODITY_DESC   CLASS_DESC  \
0      CENSUS       CROPS   VEGETABLES          BEANS         SNAP   
1      CENSUS       CROPS  FIELD CROPS         COTTON  ALL CLASSES   
2      CENSUS       CROPS  FIELD CROPS         COTTON       UPLAND   
3      CENSUS       CROPS  FIELD CROPS         COTTON       UPLAND   
4      CENSUS       CROPS  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES   

        PRODN_PRACTICE_DESC         UTIL_PRACTICE_DESC STATISTICCAT_DESC  \
0  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
1  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
2  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
3                 IRRIGATED  ALL UTILIZATION PRACTICES    AREA HARVESTED   
4  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   

  UNIT_DESC                                   SHORT_DESC DOMAIN_DESC  \
0     ACRES                BEANS, SNAP - ACRES HARVESTED       TOTAL   
1     ACRES                     COTTON - ACRES HARVESTED       TOTAL   
2     ACRES             COTTON, UPLAND - ACRES HARVESTED       TOTAL   
3     ACRES  COTTON, UPLAND, IRRIGATED - ACRES HARVESTED       TOTAL   
4     ACRES              HAY & HAYLAGE - ACRES HARVESTED       TOTAL   

  DOMAINCAT_DESC AGG_LEVEL_DESC  STATE_ANSI  STATE_FIPS_CODE STATE_ALPHA  \
0  NOT SPECIFIED         COUNTY         1.0              1.0          AL   
1  NOT SPECIFIED         COUNTY         1.0              1.0          AL   
2  NOT SPECIFIED         COUNTY         1.0              1.0          AL   
3  NOT SPECIFIED         COUNTY         1.0              1.0          AL   
4  NOT SPECIFIED         COUNTY         1.0              1.0          AL   

  STATE_NAME  ASD_CODE         ASD_DESC  COUNTY_ANSI  COUNTY_CODE COUNTY_NAME  \
0    ALABAMA      10.0  NORTHERN VALLEY         33.0         33.0     COLBERT   
1    ALABAMA      10.0  NORTHERN VALLEY         33.0         33.0     COLBERT   
2    ALABAMA      10.0  NORTHERN VALLEY         33.0         33.0     COLBERT   
3    ALABAMA      10.0  NORTHERN VALLEY         33.0         33.0     COLBERT   
4    ALABAMA      10.0  NORTHERN VALLEY         33.0         33.0     COLBERT   

  REGION_DESC ZIP_5  WATERSHED_CODE WATERSHED_DESC CONGR_DISTRICT_CODE  \
0        None  None             0.0           None                None   
1        None  None             0.0           None                None   
2        None  None             0.0           None                None   
3        None  None             0.0           None                None   
4        None  None             0.0           None                None   

   COUNTRY_CODE   COUNTRY_NAME                      LOCATION_DESC    YEAR  \
0        9000.0  UNITED STATES  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0   
1        9000.0  UNITED STATES  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0   
2        9000.0  UNITED STATES  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0   
3        9000.0  UNITED STATES  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0   
4        9000.0  UNITED STATES  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0   

  FREQ_DESC  BEGIN_CODE  END_CODE REFERENCE_PERIOD_DESC WEEK_ENDING  \
0    ANNUAL         0.0       0.0                  YEAR        None   
1    ANNUAL         0.0       0.0                  YEAR        None   
2    ANNUAL         0.0       0.0                  YEAR        None   
3    ANNUAL         0.0       0.0                  YEAR        None   
4    ANNUAL         0.0       0.0                  YEAR        None   

             LOAD_TIME   VALUE  CV_%  __index_level_0__  
0  2012-01-01 00:00:00     (D)  None                  0  
1  2012-01-01 00:00:00  24,598  None                  1  
2  2012-01-01 00:00:00  24,598  None                  2  
3  2012-01-01 00:00:00     (D)  None                  3  
4  2012-01-01 00:00:00  12,055  None                  4

In [2]:
df_2002 = spark.read.parquet("census_02.parquet")

# Parquet files can also be used to create a temporary view and then used in SQL statements.
df_2002.createOrReplaceTempView("df_2002")

In [6]:
interesting_column_str = 'GROUP_DESC, COMMODITY_DESC, CLASS_DESC, PRODN_PRACTICE_DESC, UTIL_PRACTICE_DESC, STATISTICCAT_DESC, UNIT_DESC, \
SHORT_DESC, LOCATION_DESC, DOMAIN_DESC, VALUE'
interesting_column_list = str.split(interesting_column_str)
interesting_columns_fewer_coulumns_str = 'GROUP_DESC, COMMODITY_DESC, STATISTICCAT_DESC, UNIT_DESC, \
SHORT_DESC, LOCATION_DESC, DOMAIN_DESC, VALUE'
interesting_columns_fewer_coulumns_list = interesting_columns_fewer_coulumns_str.split()
print(interesting_columns_fewer_coulumns_list)

['GROUP_DESC,', 'COMMODITY_DESC,', 'STATISTICCAT_DESC,', 'UNIT_DESC,', 'SHORT_DESC,', 'LOCATION_DESC,', 'DOMAIN_DESC,', 'VALUE']


In [4]:
only_crops_2002_df = spark.sql("SELECT {} FROM df_2002 WHERE SECTOR_DESC='CROPS'".format(interesting_column_str))
only_crops_2002_df.createOrReplaceTempView("only_crops_2002_df")

In [5]:
check_other_COMMOD_DESC_2002_df = spark.sql("SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%OTHER%'".format(interesting_column_str))
check_other_COMMOD_DESC_2002_df.createOrReplaceTempView("check_other_COMMOD_DESC_2002_df")
check_other_COMMOD_DESC_2002_df.toPandas().tail(10000)

GROUP_DESC            COMMODITY_DESC       CLASS_DESC  \
9767         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9768         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9769         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9770         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9771         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9772         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9773         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9774         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9775         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9776         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9777         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9778         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9779         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9780         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9781         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9782         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9783         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9784         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9785         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9786         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9787         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9788         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9789         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9790         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9791         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9792         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9793         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9794         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9795         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9796         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9797         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9798         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9799         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9800         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9801         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9802         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9803         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9804         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9805         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9806         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9807         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9808         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9809         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9810         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9811         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9812         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9813         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9814         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9815         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9816         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9817         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9818         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9819         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9820         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9821         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9822          VEGETABLES         VEGET

In [7]:
check_woody_COMMOD_DESC_2002_df = spark.sql("SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%CHRISTMASS TREES%' OR COMMODITY_DESC LIKE '%WOODY%'".format(interesting_columns_fewer_coulumns_str))
check_woody_COMMOD_DESC_2002_df.createOrReplaceTempView("check_woody_COMMOD_DESC_2002_df")
check_woody_COMMOD_DESC_2002_df.toPandas().tail(10000)

GROUP_DESC                                COMMODITY_DESC  \
0     HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
1     HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
2     HORTICULTURE                        SHORT TERM WOODY CROPS   
3     HORTICULTURE                        SHORT TERM WOODY CROPS   
4     HORTICULTURE                        SHORT TERM WOODY CROPS   
5     HORTICULTURE                        SHORT TERM WOODY CROPS   
6     HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
7     HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
8     HORTICULTURE                        SHORT TERM WOODY CROPS   
9     HORTICULTURE                        SHORT TERM WOODY CROPS   
10    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
11    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
12    HORTICULTURE                        SHORT TERM WOODY CROPS   
13    HORTICULTURE                        SHORT TERM WOODY CROPS   
14    HORTICULTURE                        SHORT TERM WOODY CROPS   
15    HORTICULTURE                        SHORT TERM WOODY CROPS   
16    HORTICULTURE                        SHORT TERM WOODY CROPS   
17    HORTICULTURE                        SHORT TERM WOODY CROPS   
18    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
19    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
20    HORTICULTURE                        SHORT TERM WOODY CROPS   
21    HORTICULTURE                        SHORT TERM WOODY CROPS   
22    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
23    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
24    HORTICULTURE                        SHORT TERM WOODY CROPS   
25    HORTICULTURE                        SHORT TERM WOODY CROPS   
26    HORTICULTURE                        SHORT TERM WOODY CROPS   
27    HORTICULTURE                        SHORT TERM WOODY CROPS   
28    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
29    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
30    HORTICULTURE                        SHORT TERM WOODY CROPS   
31    HORTICULTURE                        SHORT TERM WOODY CROPS   
32    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
33    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
34    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
35    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
36    HORTICULTURE                        SHORT TERM WOODY CROPS   
37    HORTICULTURE                        SHORT TERM WOODY CROPS   
38    HORTICULTURE                        SHORT TERM WOODY CROPS   
39    HORTICULTURE                        SHORT TERM WOODY CROPS   
40    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
41    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
42    HORTICULTURE                        SHORT TERM WOODY CROPS   
43    HORTICULTURE                        SHORT TERM WOODY CROPS   
44    HORTICULTURE                        SHORT TERM WOODY CROPS   
45    HORTICULTURE                        SHORT TERM WOODY CROPS   
46    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
47    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
48    HORTICULTURE                        SHORT TERM WOODY CROPS   
49    HORTICULTURE                        SHORT TERM WOODY CROPS   
50    HORTICULTURE                        SHORT TERM WOODY CROPS   
51    HORTICULTURE                        SHORT TERM WOODY CROPS   
52    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
53    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
54    HORTICULTURE                        SHORT TERM WOODY CROPS   
55    HORTICULTURE                        SHORT TERM WOODY CROPS   
56    HORTICULTURE                        SHORT TERM WOODY CROPS   
57    HORTICULTURE                        SHORT TERM WOODY CROPS

In [25]:
check_output_df = spark.sql("SELECT DISTINCT COMMODITY_DESC FROM only_crops_2002_df")
check_output_df.take(100000)

[Row(COMMODITY_DESC='TANGELOS'),
 Row(COMMODITY_DESC='OATS'),
 Row(COMMODITY_DESC='TEMPLES'),
 Row(COMMODITY_DESC='PEAS'),
 Row(COMMODITY_DESC='PASSION FRUIT'),
 Row(COMMODITY_DESC='CRAMBE'),
 Row(COMMODITY_DESC='SORGHUM'),
 Row(COMMODITY_DESC='RYE'),
 Row(COMMODITY_DESC='AMARANTH'),
 Row(COMMODITY_DESC='FIELD CROPS, OTHER'),
 Row(COMMODITY_DESC='TARO'),
 Row(COMMODITY_DESC='TANGERINES'),
 Row(COMMODITY_DESC='ARTICHOKES'),
 Row(COMMODITY_DESC='PAPAYAS'),
 Row(COMMODITY_DESC='CUCUMBERS'),
 Row(COMMODITY_DESC='BOYSENBERRIES'),
 Row(COMMODITY_DESC='POMEGRANATES'),
 Row(COMMODITY_DESC='PEACHES'),
 Row(COMMODITY_DESC='CARROTS'),
 Row(COMMODITY_DESC='BEANS'),
 Row(COMMODITY_DESC='POTATOES'),
 Row(COMMODITY_DESC='VEGETABLE TOTALS'),
 Row(COMMODITY_DESC='BLACKBERRIES'),
 Row(COMMODITY_DESC='GRASSES & LEGUMES, OTHER'),
 Row(COMMODITY_DESC='GRASSES & LEGUMES TOTALS'),
 Row(COMMODITY_DESC='FLAXSEED'),
 Row(COMMODITY_DESC='FRUIT & TREE NUTS, OTHER'),
 Row(COMMODITY_DESC='WILD RICE'),
 Row(COMMODIT

In [ ]:
to_check_list =  ['FIELD CROPS, OTHER','GRASSES & LEGUMES, OTHER', 'FRUIT & TREE NUTS, OTHER', 'SHORT TERM WOODY CROPS', 'CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS', ]

In [17]:
only_crops_2002_df.toPandas().tail()

GROUP_DESC          COMMODITY_DESC   CLASS_DESC  \
737326  FIELD CROPS  GRAIN STORAGE CAPACITY  ALL CLASSES   
737327  FIELD CROPS  GRAIN STORAGE CAPACITY  ALL CLASSES   
737328  FIELD CROPS  GRAIN STORAGE CAPACITY  ALL CLASSES   
737329  FIELD CROPS  GRAIN STORAGE CAPACITY  ALL CLASSES   
737330  FIELD CROPS  GRAIN STORAGE CAPACITY  ALL CLASSES   

             PRODN_PRACTICE_DESC UTIL_PRACTICE_DESC STATISTICCAT_DESC  \
737326  ALL PRODUCTION PRACTICES            ON FARM          CAPACITY   
737327  ALL PRODUCTION PRACTICES            ON FARM          CAPACITY   
737328  ALL PRODUCTION PRACTICES            ON FARM          CAPACITY   
737329  ALL PRODUCTION PRACTICES            ON FARM          CAPACITY   
737330  ALL PRODUCTION PRACTICES            ON FARM          CAPACITY   

         UNIT_DESC                                         SHORT_DESC  \
737326  OPERATIONS  GRAIN STORAGE CAPACITY, ON FARM - OPERATIONS W...   
737327          BU  GRAIN STORAGE CAPACITY, ON FARM - CAPACITY, ME...   
737328  OPERATIONS  GRAIN STORAGE CAPACITY, ON FARM - OPERATIONS W...   
737329          BU  GRAIN STORAGE CAPACITY, ON FARM - CAPACITY, ME...   
737330  OPERATIONS  GRAIN STORAGE CAPACITY, ON FARM - OPERATIONS W...   

                     DOMAIN_DESC          VALUE  
737326  AREA CROPLAND, HARVESTED         14,830  
737327  AREA CROPLAND, HARVESTED  2,146,607,911  
737328  AREA CROPLAND, HARVESTED         16,211  
737329  AREA CROPLAND, HARVESTED    384,986,549  
737330  AREA CROPLAND, HARVESTED          1,381